In [7]:
%reload_ext autoreload
%autoreload 2

import pandas as pd
pd.options.plotting.backend = "plotly"

import sys
sys.path.insert(0, 'driftpy/src/')

import driftpy
print(driftpy.__file__)

import numpy as np 
from sim.sim import DriftSim, SimpleDriftSim, load_hist_oracle

import os
import datetime
from sim.agents import * 
from programs.clearing_house.state import * 
from sim.events import OpenPositionEvent
from sim.helpers import random_walk_oracle, rand_heterosk_oracle, class_to_json
import pickle as cPickle

/Users/brennan/Documents/drift/simulation/drift-sim/driftpy/src/driftpy/__init__.py


In [8]:
def make_clearing_house(
    base_spread, 
    oracle=None,
):
    # generate random oracle data 
    if oracle is None: 
        prices, timestamps = random_walk_oracle(1)
        oracle = Oracle(prices=prices, timestamps=timestamps)
    
    # create the market with/without spread 
    amm = AMM(
        oracle=oracle, 
        base_asset_reserve=int(10_000_000 * AMM_RESERVE_PRECISION), 
        quote_asset_reserve=int(10_000_000 * AMM_RESERVE_PRECISION),
        funding_period=60*60,
        peg_multiplier=int(oracle.get_price(0) * PEG_PRECISION),
        base_spread=base_spread
    )
    market = Market(amm)
        
    # create clearing house 
    fee_structure = FeeStructure(numerator=1, denominator=1000)
    clearing_house = ClearingHouse([market], fee_structure)
    clearing_house.name = f''

    return clearing_house
    
# agent which always pushes mark => oracle 
arb = Arb(
    intensity=0.8, 
    market_index=0, 
    user_index=0,
)

# random trader 
noise = Noise(
    intensity=1, 
    market_index=0, 
    user_index=0,
    size=1_000, # 1k trades
)

ch = make_clearing_house(base_spread=0)
market = ch.markets[0]
peg = market.amm.peg_multiplier / PEG_PRECISION
sqrt_k = market.amm.sqrt_k / 1e13
full_amm_position_quote = sqrt_k * peg * 2 * 1e6

# deposit_amount = 1_000 * QUOTE_PRECISION
deposit_amount = full_amm_position_quote

lp = LP(
    lp_start_time=0, 
    lp_duration=300, 
    deposit_amount=deposit_amount, 
    user_index=1, 
    market_index=0,
)

agents = [
    arb,
    noise,
    lp,
]
os.makedirs("sim-results/", exist_ok=True)

sim = SimpleDriftSim(
    "sim-results/lp",
    clearing_house=ch,
    agents=agents
)

sim.run()
results = sim.to_df(save=True)
results.head()

running simulation for 492 timesteps
running sim from timestamp 0 to 492
skipping time step: 0 ... ch time: 4
skipping time step: 1 ... ch time: 4
skipping time step: 2 ... ch time: 4
skipping time step: 3 ... ch time: 4
NOW:  9
short 2508728.646185 LUNA-PERP @ 2.4991271353814724 ( 2.2711405232 )
NOW:  10
short 533143.146611 LUNA-PERP @ 2.2226898866640634 ( 2.175272856 )
NOW:  11
short 108137.63277 LUNA-PERP @ 2.1656552411407217 ( 2.156080149 )
NOW:  12
short 21706.900847 LUNA-PERP @ 2.154158102341858 ( 2.1522377691 )
NOW:  13
long 1247953.616376 LUNA-PERP @ 2.262639840338895 ( 2.3787051415 )
NOW:  14
long 242112.070278 LUNA-PERP @ 2.4012226533553 ( 2.4239533225 )
NOW:  15
long 48102.367334 LUNA-PERP @ 2.428469408772281 ( 2.432993909 )
NOW:  16
short 2481556.962417 LUNA-PERP @ 2.1995790967177213 ( 1.9885574661 )
NOW:  17
long 3900608.601098 LUNA-PERP @ 2.3202495448519085 ( 2.707267978 )
NOW:  18
long 714286.687108 LUNA-PERP @ 2.778139511838353 ( 2.8508663383 )
NOW:  19
short 8578810.51

100%|██████████| 1468/1468 [00:00<00:00, 3924.90it/s]


m0_mark_price  m0_oracle_price  m0_bid_price  m0_ask_price  m0_wouldbe_peg  \
0           2.75         2.750702          2.75          2.75            2.75   
1           2.75         2.750702          2.75          2.75            2.75   
2           2.75         2.750702          2.75          2.75            2.75   
3           2.75         2.750702          2.75          2.75            2.75   
4           2.75         2.750702          2.75          2.75            2.75   

   m0_wouldbe_peg_cost  m0_predicted_long_funding  m0_predicted_short_funding  \
0                  0.0              -1.064084e-07               -1.064084e-07   
1                  0.0              -1.064084e-07               -1.064084e-07   
2                  0.0              -1.064084e-07               -1.064084e-07   
3                  0.0              -1.064084e-07               -1.064084e-07   
4                  0.0              -1.064084e-07               -1.064084e-07   

   m0_last_mid_price_twap  m0_repeg_to_oracle_cost  ...  \
0                    2.75                      0.0  ...   
1                    2.75                      0.0  ...   
2                    2.75                      0.0  ...   
3                    2.75                      0.0  ...   
4                    2.75                      0.0  ...   

   u0_m0_last_cumulative_funding_rate  u0_m0_last_funding_rate_ts  u0_m0_upnl  \
0                                 NaN                         NaN         NaN   
1                                 NaN                         NaN         NaN   
2                                 NaN                         NaN         NaN   
3                                 NaN                         NaN         NaN   
4                                 NaN                         NaN         NaN   

   u0_m0_ufunding  u1_m0_base_asset_amount  u1_m0_quote_asset_amount  \
0             NaN                      NaN                       NaN   
1             NaN                      NaN                       NaN   
2             NaN                      NaN                       NaN   
3             NaN                      NaN                       NaN   
4             NaN                      NaN                       NaN   

   u1_m0_last_cumulative_funding_rate  u1_m0_last_funding_rate_ts  u1_m0_upnl  \
0                                 NaN                         NaN         NaN   
1                                 NaN                         NaN         NaN   
2                                 NaN                         NaN         NaN   
3                                 NaN                         NaN         NaN   
4                                 NaN                         NaN         NaN   

   u1_m0_ufunding  
0             NaN  
1             NaN  
2             NaN  
3             NaN  
4             NaN  

[5 rows x 90 columns]

In [11]:
keep_columns = results.columns
keep_columns = [c for c in keep_columns if results[c].dtype == float or results[c].dtype == int]
# keep_columns = [c for c in keep_columns if 'u1' in c] # only lp 
filtered_df = results[keep_columns]
filtered_df.plot()